## 1) Get data

From world press photo we get:

### PHOTOGRAPHER

Da worldpress photo sitemap abbiamo estratto tutti i link a pagine di fotografi. Per ogni pagina abbiamo mandato una richiesta per ottenere il nome del fotografo, la sua nazionalità e una breve descrizione. Successivamente abbiamo analizzato la descrizione con spicy estraendo persone, organizazioni e luoghi associati all'artista. (!!!ATTENZIONE spicy potrebbe sbagliare)

In [10]:
import requests
from bs4 import BeautifulSoup
import pprint as pp

url = 'https://www.worldpressphoto.org/sitemap.xml'

r = requests.get(url)
sp = BeautifulSoup(r.text, 'html')

links = sp.find_all('loc')
photographers = []

for link in links:
    if 'person' in link.text:
        photographers.append(str(link.text))
print(photographers)

['https://www.worldpressphoto.org/person/detail/593/a-new-age-of-walls-team', 'https://www.worldpressphoto.org/person/detail/594/a-wildenberg', 'https://www.worldpressphoto.org/person/detail/595/aapo-huhta', 'https://www.worldpressphoto.org/person/detail/596/aaron-goodman', 'https://www.worldpressphoto.org/person/detail/597/aaron-huey', 'https://www.worldpressphoto.org/person/detail/41993/abbas-kowsari', 'https://www.worldpressphoto.org/person/detail/598/abbie-trayler-smith', 'https://www.worldpressphoto.org/person/detail/39116/abby-nicolas', 'https://www.worldpressphoto.org/person/detail/599/abd-doumany', 'https://www.worldpressphoto.org/person/detail/600/abdellah-azizi', 'https://www.worldpressphoto.org/person/detail/601/abdolla-heidari', 'https://www.worldpressphoto.org/person/detail/602/abdullah-doma', 'https://www.worldpressphoto.org/person/detail/603/abdurrauf-ben-madi', 'https://www.worldpressphoto.org/person/detail/604/abir-abdullah', 'https://www.worldpressphoto.org/person/det

In [11]:
import pandas as pd

data = dict()

pho_name_tot = []
nationality_tot = []
description_tot = []

for url in photographers:
        page = requests.get(url)
        
        soup = BeautifulSoup(page.content, "html.parser")

        for photographer in soup.select('div.text-widget h1'):
            pho_name = photographer.text

        n = 'none'
        for nationality in soup.select('div.paragraph'):
            if nationality:
                n = nationality.text
                n = n.strip()
           

        txt = []
        for description in soup.select('div.text-widget p'):
            txt.append(description.text)

        full_txt = " ".join(txt)

        pho_name_tot.append(pho_name)
        nationality_tot.append(n)
        description_tot.append(full_txt)

data["photographer"] = pho_name_tot
data["nationality"] = nationality_tot
data["description"] = description_tot

print(data)

{'photographer': ['A New Age of Walls team', 'A. Wildenberg', 'Aapo Huhta', 'Aaron Goodman', 'Aaron Huey', 'Abbas Kowsari', 'Abbie Trayler-Smith', 'Abby Nicolas', 'Abd Doumany', 'Abdellah Azizi', 'Abdolla Heidari', 'Abdullah Doma', 'Abdurrauf Ben Madi', 'Abir Abdullah', 'Abriansyah Liberto', 'Achim Bussler', 'Adam Ferguson', 'Adam Nadel', 'Adam Pretty', 'Adel Hana', 'Adnaan Wasey', 'Adrees Latif', 'Adriaan Monshouwer', 'Adriana Zehbrauskas', 'Adriane Ohanesian', 'Afrim Hajrullahu', 'Agnes Dherbeys', 'Ahmed Hayman', 'Ahmed Jadallah', 'Ahmed Najm', 'Ai Mabuchi', 'Aïda Muluneh', 'Aidan Sullivan', 'Aijaz Rahi', 'Aitor Garmendia', 'Akili-Casundria Ramsess', 'Akinbode Akinbiyi', 'Akintunde Akinleye', 'Akos Stiller', 'Akram Adem', 'Al Bello', 'Ala Kheir', 'Alain Ernoult', 'Alain Keler', 'Alain Le Garsmeur', 'Alain Mingam', 'Alain Noguès', 'Alain Raffestin', 'Alain Schroeder', 'Alan Diaz', 'Alan Stoga', 'Albert Facelly', 'Albert Roosenburg', 'Albert Winkler', 'Alberto Garcia', 'Alejandro Caste

In [30]:
data_worldpress_photographer = pd.DataFrame(data)
data_worldpress_photographer = data_worldpress_photographer.drop_duplicates()
data_worldpress_photographer

photographer nationality  \
0     A New Age of Walls team        none   
1               A. Wildenberg      France   
2                  Aapo Huhta     Finland   
3               Aaron Goodman        none   
4                  Aaron Huey         USA   
...                       ...         ...   
2442             Zoltán Pólya     Hungary   
2443          Zoubeir Souissi     Tunisia   
2444         Zsolt Szigetváry     Hungary   
2445                Zvi Roger      Israel   
2446        Zygmunt Wdowinski      Poland   

                                            description  
0     In the United States, Donald Trump’s call to b...  
1                                                        
2     Aapo Huhta received his MA in photography from...  
3     His research and documentary production focus ...  
4     Aaron Huey is a National Geographic photograph...  
...                                                 ...  
2442                                                     
2443  Zoubeir Souissi (Tunisia, 1968) worked for ten...  
2444                                                     
2445                                                     
2446                                                     

[2445 rows x 3 columns]

In [34]:
import spacy
from spacy import displacy

NER = spacy.load("en_core_web_sm")
pearsons = []
tot_pearsons = []
organizations = []
tot_organizations = []
places = []
tot_places = []

for x in data_worldpress_photographer['description']:
    parsed = NER(x)
    person = set()
    organization = set()
    place = set()
    for word in parsed.ents:
          
        if word.label_ == 'PERSON':
            person.add(word.text)
        if word.label_ == 'ORG':
            organization.add(word.text)
        if word.label_ == 'GPE':
            place.add(word.text)
    pearsons.append(person)
    tot_pearsons.append(len(person))
    organizations.append(organization)
    tot_organizations.append(len(organization))
    places.append(place)
    tot_places.append(len(place))

data_worldpress_photographer['persons'] = pearsons
data_worldpress_photographer['tot_persons'] = tot_pearsons
data_worldpress_photographer['organizations'] = organizations
data_worldpress_photographer['tot_organizations'] = tot_organizations
data_worldpress_photographer['places'] = places
data_worldpress_photographer['tot_places'] = tot_places

data_worldpress_photographer = data_worldpress_photographer.astype(str)
data_worldpress_photographer.to_csv('WPphotographer.csv')

In [35]:
data_worldpress_photographer

photographer nationality  \
0     A New Age of Walls team        none   
1               A. Wildenberg      France   
2                  Aapo Huhta     Finland   
3               Aaron Goodman        none   
4                  Aaron Huey         USA   
...                       ...         ...   
2442             Zoltán Pólya     Hungary   
2443          Zoubeir Souissi     Tunisia   
2444         Zsolt Szigetváry     Hungary   
2445                Zvi Roger      Israel   
2446        Zygmunt Wdowinski      Poland   

                                            description  \
0     In the United States, Donald Trump’s call to b...   
1                                                         
2     Aapo Huhta received his MA in photography from...   
3     His research and documentary production focus ...   
4     Aaron Huey is a National Geographic photograph...   
...                                                 ...   
2442                                                      
2443  Zoubeir Souissi (Tunisia, 1968) worked for ten...   
2444                                                      
2445                                                      
2446                                                      

                                                persons tot_persons  \
0     {'Zoeann Murphy', 'Reem Akkad', 'Douglas Jehl'...          12   
1                                                 set()           0   
2                                        {'Aapo Huhta'}           1   
3                       {'Alert Net', 'Calgary Herald'}           2   
4                                        {'Aaron Huey'}           1   
...                                                 ...         ...   
2442                                              set()           0   
2443                    {'Zoubeir Souissi', 'Réalités'}           2   
2444                                              set()           0   
2445                                              set()           0   
2446                                              set()           0   

                                          organizations tot_organizations  \
0      {'The Washington Post’s', 'The Washington Post'}                 2   
1                                                 set()                 0   
2     {'the Aalto University of Arts and Design', 'M...                 4   
3     {'Ottawa Citizen', 'National Post', 'PBS Front...                12   
4     {'Harper', 'Harper’s Magazine', 'National Geog...                 3   
...                                                 ...               ...   
2442                                              set()                 0   
2443      {'Reuters', 'the international press agency'}                 2   
2444                                              set()                 0   
2445                                              set()                 0   
2446                                              set()                 0   

                                                 places tot_places  
0     {'Berlin', 'Israel', 'Mexico', 'US', 'the Unit...          5  
1                                                 set()          0  
2                    {'Berlin', 'Stockholm', 'Finland'}          3  
3                                                 set()          0  
4                         {'USA', 'America', 'Seattle'}          3  
...                                                 ...        ...  
2442                                              set()          0  
2443                                        {'Tunisia'}          1  
2444                                              set()          0  
2445                                              set()          0  
2446                                              set()          0  

[2445 rows x 9 columns]

In [36]:
import pandas_profiling as pp
pp.ProfileReport(data_worldpress_photographer)

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.89it/s]


Alcuni forografi si ripetono più volte ma con informazioni mancanti. Abbiamo quindi deciso di considerare solo quelli che hanno la nazionalità associata. 

In [16]:
unique_photographer = set()

for x,y in data_worldpress_photographer.iterrows():
    p = y['photographer']
    if p in unique_photographer: 
        if y['nationality'] == 'none':
            data_worldpress_photographer.drop(data_worldpress_photographer.index[data_worldpress_photographer['nationality'] == 'none'], inplace=True)
    else:
        unique_photographer.add(y['photographer'])

In [17]:
pp.ProfileReport(data_worldpress_photographer)

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.91it/s]


Abbiamo ancora delle ripetizioni. Andiamo quindi a controllaere.

In [26]:
data_worldpress_photographer.query("photographer == 'Almudena Toral'")

photographer nationality  \
107  Almudena Toral       Spain   
108  Almudena Toral         USA   

                                           description  
107                                                     
108  She heads the feature visuals team at Univisio...